In [1]:
import numpy as np
import pandas as pd
import h5py

In [2]:
def get_2D_data_from_h5_with_dimension_check(h5_path, part_name, Slice_name):
    with h5py.File(h5_path,'r') as h5:
        X_Axis = h5[part_name][Slice_name]['X-Axis']
        Y_Axis = h5[part_name][Slice_name]['Y-Axis']
        Area = h5[part_name][Slice_name]['Area']
        Intensity = h5[part_name][Slice_name]['Intensity']

        X_Axis_size = X_Axis.size
        Y_Axis_size = Y_Axis.size
        Area_size = Area.size
        Intensity_size = Intensity.size

        #if dimensions aren't equal the following code block is entered
        if not X_Axis_size == Y_Axis_size == Area_size == Intensity_size:

            #determine the lowest value among the different sizes
            size_arr = np.array([X_Axis_size, Y_Axis_size, Area_size, Intensity_size])
            min_size = size_arr.min()

            if X_Axis_size != min_size:
                diff_size_x = X_Axis_size - min_size #calculating the difference between the actual value and the minimum and substracting it from the array
                X_Axis_new = np.delete(X_Axis, -diff_size_x)
                X_Axis = X_Axis_new
                X_Axis_size = X_Axis.size

            if Y_Axis_size != min_size:
                diff_size_y = Y_Axis_size - min_size
                Y_Axis_new = np.delete(Y_Axis, -diff_size_y)
                Y_Axis = Y_Axis_new
                Y_Axis_size = Y_Axis.size

            if Area_size != min_size:
                diff_size_area = Area_size - min_size
                Area_new = np.delete(Area, -diff_size_area)
                Area = Area_new
                Area_size = Area.size

            if Intensity_size != min_size:
                diff_size_intensity = Intensity_size - min_size
                Intensity_new = np.delete(Intensity, -diff_size_intensity)
                Intensity = Intensity_new
                Intensity_size = Intensity.size


        #by reducing all the dimensions to the minimum equal dimensions are guaranteed
        #there is a risk of deleting more than just one datapoint without noticing -> maybe add an alert after more than 5(?) while iterations
        help_arr = np.column_stack((X_Axis, Y_Axis, Area, Intensity))
        df = pd.DataFrame(help_arr, columns=['x','y','area','intensity'])
        return df

In [3]:
df_undocked = get_2D_data_from_h5_with_dimension_check('/home/jan/Documents/CodeTDMStoHDF/Ausgangsdaten/examplerRun.h5', '0_00003_Canti3_cls', 'Slice00001')

In [4]:
def get_true_min_maxX (h5_path, part_name, max_slice_number):

    minX = []
    maxX = []
    for num_slice in range(max_slice_number):
        with h5py.File(h5_path,'r') as h5:
            X_Axis = h5[part_name]['Slice'+str("{:05d}".format(num_slice+1))]['X-Axis']
            x_axis_array = np.array(X_Axis)
            minX.append(x_axis_array.min())
            maxX.append(x_axis_array.max())
    minX_array = np.asarray(minX)
    maxX_array = np.asarray(maxX)
    return minX_array.min(), maxX_array.max()

In [5]:
def get_true_min_maxY (h5_path, part_name, max_slice_number):

    minY = []
    maxY = []
    for num_slice in range(max_slice_number):
        with h5py.File(h5_path,'r') as h5:
            Y_Axis = h5[part_name]['Slice'+str("{:05d}".format(num_slice+1))]['Y-Axis']
            y_axis_array = np.array(Y_Axis)
            minY.append(y_axis_array.min())
            maxY.append(y_axis_array.max())
    minY_array = np.asarray(minY)
    maxY_array = np.asarray(maxY)
    return minY_array.min(), maxY_array.max()

In [6]:
minX = get_true_min_maxX('/home/jan/Documents/CodeTDMStoHDF/Ausgangsdaten/examplerRun.h5', '0_00003_Canti3_cls', 142)[0]
minY = get_true_min_maxY('/home/jan/Documents/CodeTDMStoHDF/Ausgangsdaten/examplerRun.h5', '0_00003_Canti3_cls', 142)[0]

In [7]:
def dock_df_to_zero(df, minX, minY):
    if minX >= 0 and minY >=0:
        df['x'] = df['x'] - minX
        df['y'] = df['y'] - minY
    elif minX < 0 and minY <0:
        df['x'] = df['x'] + abs(minX)
        df['y'] = df['y'] + abs(minY)
    elif minX >= 0 and minY <0:
        df['x'] = df['x'] - minX
        df['y'] = df['y'] + abs(minY)
    elif minX < 0 and min >= 0:
        df['x'] = df['x'] + abs(minX)
        df['y'] = df['y'] - minY
    return df

In [8]:
df_docked = dock_df_to_zero(df_undocked, minX, minY)
df_docked.describe()

x              y           area      intensity
count  143201.000000  143201.000000  143201.000000  143201.000000
mean     4232.300781    4432.887207     144.456787     299.727081
std       544.545471    2567.269775     145.760574     287.940796
min         0.000000       0.000000       0.000000       0.000000
25%      3854.000000    2287.000000       0.000000       0.000000
50%      4254.000000    4303.000000     181.000000     493.000000
75%      4653.000000    6583.000000     237.000000     553.000000
max      4946.000000    8996.000000    1080.000000    3023.000000

In [9]:
def fill_2D_voxel_area (voxel_size, num_voxels_x, num_voxels_y, df, filling_method):
    counter = 0
    array_area = np.zeros([voxel_size,voxel_size]) #creating an empty array of dimensions voxel_size*voxel_size
    for i in range(voxel_size*num_voxels_x, voxel_size*(num_voxels_x+1)): #iterating over x
        for j in range(voxel_size*num_voxels_y,voxel_size*(num_voxels_y+1)): #iterating over y
            
            print('i: ' + str(i))
            print('j: ' + str(j))

            if df[(df['x'] == i) & (df['y'] == j)].shape[0] == 1: #here subset of the original dataframe is created an filtrered --> shape[0] returns the number of rows of this df subset
                #finding the area value for a certain point in the part-data-dataframe and allocating it to a position in the array
                area_i = df.loc[(df['x'] == i) & (df['y'] == j)]
                array_area[i-num_voxels_x*voxel_size][j-num_voxels_y*voxel_size] = area_i['Area']

            elif df[(df['x'] == i) & (df['y'] == j)].shape[0] > 1:
                #if there are more values than just one the maximum value is used for the voxel-datapoint; other methods of dealing with multiple values need to be considered
                array_area[i-num_voxels_x*voxel_size][j-num_voxels_y*voxel_size] = df[(df['x'] == i) & (df['y'] == j)]['area'].max()


            elif df[(df['x'] == i) & (df['y'] == j)].shape[0] == 0 and filling_method == 'Zeros':
                array_area[i-num_voxels_x*voxel_size][j-num_voxels_y*voxel_size] = 0

            #elif filling_method == 'Mean': #with this method all the missing datapoints are getting filled with the mean of the non-missing datapoints
             #   array_area[i][j] =

    return array_area
            #theoretisch nach 1145 Schluss, praktisch läuft er immer weiter

In [10]:
fill_2D_voxel_area(20, 2, 2, df_docked, 'Zeros')

i: 40
j: 40
i: 40
j: 41
i: 40
j: 42
i: 40
j: 43
i: 40
j: 44
i: 40
j: 45
i: 40
j: 46
i: 40
j: 47
i: 40
j: 48
i: 40
j: 49
i: 40
j: 50
i: 40
j: 51
i: 40
j: 52
i: 40
j: 53
i: 40
j: 54
i: 40
j: 55
i: 40
j: 56
i: 40
j: 57
i: 40
j: 58
i: 40
j: 59
i: 41
j: 40
i: 41
j: 41
i: 41
j: 42
i: 41
j: 43
i: 41
j: 44
i: 41
j: 45
i: 41
j: 46
i: 41
j: 47
i: 41
j: 48
i: 41
j: 49
i: 41
j: 50
i: 41
j: 51
i: 41
j: 52
i: 41
j: 53
i: 41
j: 54
i: 41
j: 55
i: 41
j: 56
i: 41
j: 57
i: 41
j: 58
i: 41
j: 59
i: 42
j: 40
i: 42
j: 41
i: 42
j: 42
i: 42
j: 43
i: 42
j: 44
i: 42
j: 45
i: 42
j: 46
i: 42
j: 47
i: 42
j: 48
i: 42
j: 49
i: 42
j: 50
i: 42
j: 51
i: 42
j: 52
i: 42
j: 53
i: 42
j: 54
i: 42
j: 55
i: 42
j: 56
i: 42
j: 57
i: 42
j: 58
i: 42
j: 59
i: 43
j: 40
i: 43
j: 41
i: 43
j: 42
i: 43
j: 43
i: 43
j: 44
i: 43
j: 45
i: 43
j: 46
i: 43
j: 47
i: 43
j: 48
i: 43
j: 49
i: 43
j: 50
i: 43
j: 51
i: 43
j: 52
i: 43
j: 53
i: 43
j: 54
i: 43
j: 55
i: 43
j: 56
i: 43
j: 57
i: 43
j: 58
i: 43
j: 59
i: 44
j: 40
i: 44
j: 41
i: 44
j: 42
i: 4

array([[0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 0.,
        0., 0., 0., 0.],
       [0., 0., 0., 0., 0., 0.

In [9]:
df_docked

x       y  area  intensity
0          0.0  8977.0   0.0        0.0
1          0.0  8977.0   0.0        0.0
2          0.0  8977.0   0.0        0.0
3          0.0  8977.0   0.0        0.0
4          0.0  8977.0   0.0        0.0
...        ...     ...   ...        ...
143196  3528.0  8977.0   0.0        0.0
143197  3528.0  8977.0   0.0        0.0
143198  3528.0  8977.0   0.0        0.0
143199  3528.0  8977.0   0.0        0.0
143200  3528.0  8977.0   0.0        0.0

[143201 rows x 4 columns]

In [10]:
 #Syntax: DataFrame.drop_duplicates(subset=None, keep=’first’, inplace=False)
df_1 = df_docked.drop_duplicates()    
df_1

x       y   area  intensity
0          0.0  8977.0    0.0        0.0
655       18.0  8950.0    0.0        0.0
656       29.0  8932.0    0.0        0.0
657       46.0  8905.0    0.0        0.0
658       58.0  8888.0    0.0        0.0
...        ...     ...    ...        ...
142958  3528.0  8977.0  162.0        0.0
142959  3528.0  8977.0  324.0        0.0
142960  3528.0  8977.0  266.0        0.0
142961  3528.0  8977.0  208.0        0.0
142963  3528.0  8977.0  104.0        0.0

[92468 rows x 4 columns]

In [11]:
df_1.loc[(df_1['area'] != 0) & (df_1['intensity'] != 0) ]

x       y   area  intensity
978     3510.0  3578.0  157.0      677.0
979     3519.0  3578.0  315.0      606.0
980     3525.0  3578.0  349.0      619.0
981     3535.0  3578.0  384.0      618.0
982     3541.0  3578.0  384.0      669.0
...        ...     ...    ...        ...
142903  3569.0  8977.0  206.0      508.0
142904  3569.0  8977.0  288.0      518.0
142905  3569.0  8977.0  370.0      501.0
142906  3569.0  8977.0  370.0      519.0
142907  3569.0  8977.0  341.0      525.0

[74102 rows x 4 columns]

In [13]:
rslt_df = df_1.loc[(df_1['area'] != 0) & (df_1['intensity'] != 0)] 
rslt_df

x       y   area  intensity
978     3510.0  3578.0  157.0      677.0
979     3519.0  3578.0  315.0      606.0
980     3525.0  3578.0  349.0      619.0
981     3535.0  3578.0  384.0      618.0
982     3541.0  3578.0  384.0      669.0
...        ...     ...    ...        ...
142903  3569.0  8977.0  206.0      508.0
142904  3569.0  8977.0  288.0      518.0
142905  3569.0  8977.0  370.0      501.0
142906  3569.0  8977.0  370.0      519.0
142907  3569.0  8977.0  341.0      525.0

[74102 rows x 4 columns]

In [14]:
final_df = rslt_df.astype(int)
final_df

x     y  area  intensity
978     3510  3578   157        677
979     3519  3578   315        606
980     3525  3578   349        619
981     3535  3578   384        618
982     3541  3578   384        669
...      ...   ...   ...        ...
142903  3569  8977   206        508
142904  3569  8977   288        518
142905  3569  8977   370        501
142906  3569  8977   370        519
142907  3569  8977   341        525

[74102 rows x 4 columns]

In [15]:
((final_df['x'] == 3510) & (final_df['y'] == 3578)).any()

True

In [16]:
final_df.loc[(final_df['x']== 3569) & (final_df['y'] == 8977)]

#df_1.loc[(df_1['area'] != 0) & (df_1['intensity'] != 0)]

x     y  area  intensity
142902  3569  8977   238        555
142903  3569  8977   206        508
142904  3569  8977   288        518
142905  3569  8977   370        501
142906  3569  8977   370        519
142907  3569  8977   341        525

In [50]:
#build a dataframe containing the maximum values of both columns in one row and dropping all the other rows 
# erst checken, ob mehrere Datenpunkte vorhanden sind
# dann max area herausfiltern
# dann max intensity herausfiltern 
# neuen Eintrag machen und alte Einträge löschen 

final_df.loc[(final_df['x']== 3569) & (final_df['y'] == 8977)].shape[0] # <- so kriegt man die Anzahl an Reihen raus


6

In [47]:
final_df_dupl = final_df[final_df.duplicated(['x','y'])]
final_df[final_df.duplicated(['x','y'])].index
#final_df_dupl.shape[0]
#print(final_df_dupl.iloc[1])
#((final_df['x'] == 3510) & (final_df['y'] == 3578)).any()
#area = final_df.loc[(final_df['x']== 3510) & (final_df['y'] == 3578)]['area'].mean().astype(int)
#print(area)

Int64Index([  1169,   1353,   1354,   1355,   1356,   1357,   1358,   1359,
              1600,   1608,
            ...
            142842, 142843, 142844, 142845, 142846, 142903, 142904, 142905,
            142906, 142907],
           dtype='int64', length=10365)

In [48]:
final_df_dupl = final_df_dupl.reset_index(drop = True)

In [49]:
final_df_dupl

x     y  area  intensity
0      4946  3528   277        520
1      3510  3528   214        676
2      3510  3528   199        617
3      3510  3528   199        543
4      3510  3528   253        510
...     ...   ...   ...        ...
10360  3569  8977   206        508
10361  3569  8977   288        518
10362  3569  8977   370        501
10363  3569  8977   370        519
10364  3569  8977   341        525

[10365 rows x 4 columns]

In [69]:
df_compact = pd.DataFrame(columns=['x','y','area','intensity'])

In [45]:
final_df_dupl.iloc[0]['x']

4946

In [ ]:
df_compact = pd.DataFrame(columns=['x','y','area','intensity'])
import time
start_time = time.time()


for ind in range(final_df_dupl.shape[0]):
    #print(ind)
    #if final_df_dupl.iloc[ind].any():
    #x = final_df_dupl.iloc[ind]['x']
    #y = final_df_dupl.iloc[ind]['y']
    #print(x)
    #print(y)
    area_mean = final_df_dupl.loc[(final_df_dupl['x']== final_df_dupl.iloc[ind]['x']) & (final_df_dupl['y'] == final_df_dupl.iloc[ind]['y'])]['area'].mean().astype(int)
    intensity_mean = final_df_dupl.loc[(final_df_dupl['x']== x) & (final_df_dupl['y'] == y)]['intensity'].mean().astype(int)
    df_compact = df_compact.append({'x': x, 'y':y, 'area':area_mean , 'intensity':intensity_mean}, ignore_index=True).drop_duplicates()
    #df_compact = df_compact.drop_duplicates()
    #print(df_compact.shape[0])
    #final_df_dupl = final_df_dupl.drop(final_df_dupl.loc[(final_df_dupl['x']== x) & (final_df_dupl['y'] == y)].index)
    #print(final_df_dupl)

final_df_dupl = final_df_dupl.reset_index(drop = True)
print("--- %s seconds ---" % (time.time() - start_time))
    
  

    
    
    
    
    
    #df = df.reset_index(level=0, drop=True).reset_index()
    
    # reindexing after every step 

In [57]:
df_compact

x     y area intensity
0     4946  3528  216       538
1     3510  3528  227       533
2     4946  3326  227       550
3     4946  3276  247       537
4     3510  3276  254       563
...    ...   ...  ...       ...
6636  3729  8977  368       542
6637  3528  8817  246       515
6638  3649  8977  415       519
6639  3528  8897  373       596
6640  3569  8977  315       514

[6641 rows x 4 columns]

In [60]:
def filter_df (df, mode ):
    #making the dataframe an integer
    df_int = df.astype(int)
    #filtering out duplicates - 'wo' is for without
    df_wo_dupl = df_int.drop_duplicates()
    #filtering out all rows with area == 0 & intensity == 0 
    df_wo_00 = df_wo_dupl.loc[(df_wo_dupl['area'] != 0) & (df_wo_dupl['intensity'] != 0)] 
    
    print(df_wo_00)
    
    #for all x and y combinations which occur multiple times select the maximum of area and intensity, delete 
    #all rows and add a row with x,y and the mean values of area and intensity <- other ways are possible too e.g. the maximum 
   
    #create an empty dataframe which is filled with the mean/max values of the area and intensity 
    df_compact = pd.DataFrame(columns=['x','y','area','intensity'])
    
    final_df_dupl = df_wo_00[df_wo_00.duplicated(['x','y'])]
       
    for x in range(final_df_dupl['x'].min(),final_df_dupl['x'].max(),1):
        for y in range (final_df_dupl['y'].min(),final_df_dupl['y'].max(),1):
            print('x = ' + str(x))
            print('y = ' + str(y))
            if ((final_df_dupl['x'] == x) & (final_df_dupl['y'] == y)).any():
                print('hit')
                if mode == 'mean':
                    area_mean = final_df_dupl.loc[(final_df_dupl['x']== x) & (final_df_dupl['y'] == y)]['area'].mean().astype(int)
                    intensity_mean = final_df_dupl.loc[(final_df_dupl['x']== x) & (final_df_dupl['y'] == y)]['intensity'].mean().astype(int)
                    df_compact.append({'x': x, 'y':y, 'area':area_mean , 'intensity':intensity_mean}, ignore_index=True)
                if mode == 'max':
                    area_max = final_df_dupl.loc[(final_df_dupl['x']== x) & (final_df_dupl['y'] == y)]['area'].max().astype(int)
                    intensity_max  = final_df_dupl.loc[(final_df_dupl['x']== x) & (final_df_dupl['y'] == y)]['intensity'].max().astype(int)
                    df_compact.append({'x': x, 'y':y, 'area':area_mean , 'intensity':intensity_mean}, ignore_index=True)
                    
    #substract the final_df_dupl from df_wo_00 and add df_compact to df_wo_00 
    df_wo_00 = df_wo_00.drop(final_df_dupl.index) 
    df_out = df_wo_00.append(df_compact, ignore_index=True)
                    
    return (df_out)                

In [74]:
final_df[final_df.duplicated(['x','y'])].drop_duplicates(subset = ['x','y']).shape[0]

6641

In [61]:
filter_df(df_docked, 'mean')

           x     y  area  intensity
978     3510  3578   157        677
979     3519  3578   315        606
980     3525  3578   349        619
981     3535  3578   384        618
982     3541  3578   384        669
...      ...   ...   ...        ...
142903  3569  8977   206        508
142904  3569  8977   288        518
142905  3569  8977   370        501
142906  3569  8977   370        519
142907  3569  8977   341        525

[74102 rows x 4 columns]
x = 3510
y = 0
hit
x = 3510
y = 1
x = 3510
y = 2
x = 3510
y = 3
hit
x = 3510
y = 4
x = 3510
y = 5
x = 3510
y = 6
x = 3510
y = 7
x = 3510
y = 8
x = 3510
y = 9
x = 3510
y = 10
x = 3510
y = 11
x = 3510
y = 12
x = 3510
y = 13
x = 3510
y = 14
x = 3510
y = 15
x = 3510
y = 16
x = 3510
y = 17
x = 3510
y = 18
x = 3510
y = 19
x = 3510
y = 20
x = 3510
y = 21
x = 3510
y = 22
x = 3510
y = 23
x = 3510
y = 24
x = 3510
y = 25
hit
x = 3510
y = 26
x = 3510
y = 27
x = 3510
y = 28
x = 3510
y = 29
x = 3510
y = 30
x = 3510
y = 31
x = 3510
y = 32
x = 3510
y =

x = 3510
y = 602
x = 3510
y = 603
x = 3510
y = 604
x = 3510
y = 605
x = 3510
y = 606
x = 3510
y = 607
x = 3510
y = 608
x = 3510
y = 609
x = 3510
y = 610
x = 3510
y = 611
x = 3510
y = 612
x = 3510
y = 613
x = 3510
y = 614
x = 3510
y = 615
x = 3510
y = 616
x = 3510
y = 617
x = 3510
y = 618
x = 3510
y = 619
x = 3510
y = 620
x = 3510
y = 621
x = 3510
y = 622
x = 3510
y = 623
x = 3510
y = 624
x = 3510
y = 625
x = 3510
y = 626
x = 3510
y = 627
x = 3510
y = 628
x = 3510
y = 629
x = 3510
y = 630
x = 3510
y = 631
x = 3510
y = 632
x = 3510
y = 633
x = 3510
y = 634
x = 3510
y = 635
x = 3510
y = 636
x = 3510
y = 637
x = 3510
y = 638
x = 3510
y = 639
x = 3510
y = 640
x = 3510
y = 641
x = 3510
y = 642
x = 3510
y = 643
x = 3510
y = 644
x = 3510
y = 645
x = 3510
y = 646
x = 3510
y = 647
x = 3510
y = 648
x = 3510
y = 649
x = 3510
y = 650
x = 3510
y = 651
x = 3510
y = 652
x = 3510
y = 653
x = 3510
y = 654
x = 3510
y = 655
x = 3510
y = 656
x = 3510
y = 657
x = 3510
y = 658
x = 3510
y = 659
x = 3510
y = 6

x = 3510
y = 1236
x = 3510
y = 1237
x = 3510
y = 1238
x = 3510
y = 1239
x = 3510
y = 1240
x = 3510
y = 1241
x = 3510
y = 1242
x = 3510
y = 1243
x = 3510
y = 1244
x = 3510
y = 1245
x = 3510
y = 1246
x = 3510
y = 1247
x = 3510
y = 1248
x = 3510
y = 1249
x = 3510
y = 1250
x = 3510
y = 1251
x = 3510
y = 1252
x = 3510
y = 1253
x = 3510
y = 1254
x = 3510
y = 1255
x = 3510
y = 1256
x = 3510
y = 1257
x = 3510
y = 1258
x = 3510
y = 1259
x = 3510
y = 1260
hit
x = 3510
y = 1261
x = 3510
y = 1262
x = 3510
y = 1263
x = 3510
y = 1264
x = 3510
y = 1265
x = 3510
y = 1266
x = 3510
y = 1267
x = 3510
y = 1268
x = 3510
y = 1269
x = 3510
y = 1270
x = 3510
y = 1271
x = 3510
y = 1272
x = 3510
y = 1273
hit
x = 3510
y = 1274
x = 3510
y = 1275
x = 3510
y = 1276
x = 3510
y = 1277
x = 3510
y = 1278
x = 3510
y = 1279
x = 3510
y = 1280
x = 3510
y = 1281
x = 3510
y = 1282
hit
x = 3510
y = 1283
x = 3510
y = 1284
x = 3510
y = 1285
x = 3510
y = 1286
x = 3510
y = 1287
x = 3510
y = 1288
x = 3510
y = 1289
x = 3510
y = 129

x = 3510
y = 1879
x = 3510
y = 1880
x = 3510
y = 1881
x = 3510
y = 1882
x = 3510
y = 1883
x = 3510
y = 1884
x = 3510
y = 1885
x = 3510
y = 1886
x = 3510
y = 1887
x = 3510
y = 1888
x = 3510
y = 1889
x = 3510
y = 1890
x = 3510
y = 1891
x = 3510
y = 1892
x = 3510
y = 1893
x = 3510
y = 1894
x = 3510
y = 1895
x = 3510
y = 1896
x = 3510
y = 1897
x = 3510
y = 1898
x = 3510
y = 1899
x = 3510
y = 1900
x = 3510
y = 1901
x = 3510
y = 1902
x = 3510
y = 1903
x = 3510
y = 1904
x = 3510
y = 1905
x = 3510
y = 1906
x = 3510
y = 1907
x = 3510
y = 1908
x = 3510
y = 1909
x = 3510
y = 1910
x = 3510
y = 1911
x = 3510
y = 1912
x = 3510
y = 1913
x = 3510
y = 1914
x = 3510
y = 1915
x = 3510
y = 1916
x = 3510
y = 1917
x = 3510
y = 1918
x = 3510
y = 1919
x = 3510
y = 1920
x = 3510
y = 1921
x = 3510
y = 1922
x = 3510
y = 1923
x = 3510
y = 1924
x = 3510
y = 1925
x = 3510
y = 1926
x = 3510
y = 1927
x = 3510
y = 1928
x = 3510
y = 1929
x = 3510
y = 1930
x = 3510
y = 1931
x = 3510
y = 1932
x = 3510
y = 1933
x = 3510
y

x = 3510
y = 2549
x = 3510
y = 2550
x = 3510
y = 2551
x = 3510
y = 2552
x = 3510
y = 2553
x = 3510
y = 2554
x = 3510
y = 2555
x = 3510
y = 2556
x = 3510
y = 2557
x = 3510
y = 2558
x = 3510
y = 2559
x = 3510
y = 2560
x = 3510
y = 2561
hit
x = 3510
y = 2562
x = 3510
y = 2563
x = 3510
y = 2564
x = 3510
y = 2565
x = 3510
y = 2566
x = 3510
y = 2567
x = 3510
y = 2568
x = 3510
y = 2569
x = 3510
y = 2570
hit
x = 3510
y = 2571
x = 3510
y = 2572
x = 3510
y = 2573
x = 3510
y = 2574
x = 3510
y = 2575
x = 3510
y = 2576
x = 3510
y = 2577
x = 3510
y = 2578
x = 3510
y = 2579
x = 3510
y = 2580
x = 3510
y = 2581
x = 3510
y = 2582
x = 3510
y = 2583
x = 3510
y = 2584
x = 3510
y = 2585
x = 3510
y = 2586
x = 3510
y = 2587
x = 3510
y = 2588
x = 3510
y = 2589
x = 3510
y = 2590
x = 3510
y = 2591
x = 3510
y = 2592
x = 3510
y = 2593
x = 3510
y = 2594
x = 3510
y = 2595
x = 3510
y = 2596
x = 3510
y = 2597
x = 3510
y = 2598
x = 3510
y = 2599
x = 3510
y = 2600
x = 3510
y = 2601
x = 3510
y = 2602
x = 3510
y = 2603
x 

...

x = 3526
y = 2241
x = 3526
y = 2242
x = 3526
y = 2243
x = 3526
y = 2244
x = 3526
y = 2245
x = 3526
y = 2246
x = 3526
y = 2247
x = 3526
y = 2248
x = 3526
y = 2249
x = 3526
y = 2250
x = 3526
y = 2251
x = 3526
y = 2252
x = 3526
y = 2253
x = 3526
y = 2254
x = 3526
y = 2255
x = 3526
y = 2256
x = 3526
y = 2257
x = 3526
y = 2258
x = 3526
y = 2259
x = 3526
y = 2260
x = 3526
y = 2261
x = 3526
y = 2262
x = 3526
y = 2263
x = 3526
y = 2264
x = 3526
y = 2265
x = 3526
y = 2266
x = 3526
y = 2267
x = 3526
y = 2268
x = 3526
y = 2269
x = 3526
y = 2270
x = 3526
y = 2271
x = 3526
y = 2272
x = 3526
y = 2273
x = 3526
y = 2274
x = 3526
y = 2275
x = 3526
y = 2276
x = 3526
y = 2277
x = 3526
y = 2278
x = 3526
y = 2279
x = 3526
y = 2280
x = 3526
y = 2281
x = 3526
y = 2282
x = 3526
y = 2283
x = 3526
y = 2284
x = 3526
y = 2285
x = 3526
y = 2286
x = 3526
y = 2287
x = 3526
y = 2288
x = 3526
y = 2289
x = 3526
y = 2290
x = 3526
y = 2291
x = 3526
y = 2292
x = 3526
y = 2293
x = 3526
y = 2294
x = 3526
y = 2295
x = 3526
y

x = 3526
y = 2883
x = 3526
y = 2884
x = 3526
y = 2885
x = 3526
y = 2886
x = 3526
y = 2887
x = 3526
y = 2888
x = 3526
y = 2889
x = 3526
y = 2890
x = 3526
y = 2891
x = 3526
y = 2892
x = 3526
y = 2893
x = 3526
y = 2894
x = 3526
y = 2895
x = 3526
y = 2896
x = 3526
y = 2897
x = 3526
y = 2898
x = 3526
y = 2899
x = 3526
y = 2900
x = 3526
y = 2901
x = 3526
y = 2902
x = 3526
y = 2903
x = 3526
y = 2904
x = 3526
y = 2905
x = 3526
y = 2906
x = 3526
y = 2907
x = 3526
y = 2908
x = 3526
y = 2909
x = 3526
y = 2910
x = 3526
y = 2911
x = 3526
y = 2912
x = 3526
y = 2913
x = 3526
y = 2914
x = 3526
y = 2915
x = 3526
y = 2916
x = 3526
y = 2917
x = 3526
y = 2918
x = 3526
y = 2919
x = 3526
y = 2920
x = 3526
y = 2921
x = 3526
y = 2922
x = 3526
y = 2923
x = 3526
y = 2924
x = 3526
y = 2925
x = 3526
y = 2926
x = 3526
y = 2927
x = 3526
y = 2928
x = 3526
y = 2929
x = 3526
y = 2930
x = 3526
y = 2931
x = 3526
y = 2932
x = 3526
y = 2933
x = 3526
y = 2934
x = 3526
y = 2935
x = 3526
y = 2936
x = 3526
y = 2937
x = 3526
y

x = 3526
y = 3548
x = 3526
y = 3549
x = 3526
y = 3550
x = 3526
y = 3551
x = 3526
y = 3552
x = 3526
y = 3553
x = 3526
y = 3554
x = 3526
y = 3555
x = 3526
y = 3556
x = 3526
y = 3557
x = 3526
y = 3558
x = 3526
y = 3559
x = 3526
y = 3560
x = 3526
y = 3561
x = 3526
y = 3562
x = 3526
y = 3563
x = 3526
y = 3564
x = 3526
y = 3565
x = 3526
y = 3566
x = 3526
y = 3567
x = 3526
y = 3568
x = 3526
y = 3569
x = 3526
y = 3570
x = 3526
y = 3571
x = 3526
y = 3572
x = 3526
y = 3573
x = 3526
y = 3574
x = 3526
y = 3575
x = 3526
y = 3576
x = 3526
y = 3577
x = 3526
y = 3578
x = 3526
y = 3579
x = 3526
y = 3580
x = 3526
y = 3581
x = 3526
y = 3582
x = 3526
y = 3583
x = 3526
y = 3584
x = 3526
y = 3585
x = 3526
y = 3586
x = 3526
y = 3587
x = 3526
y = 3588
x = 3526
y = 3589
x = 3526
y = 3590
x = 3526
y = 3591
x = 3526
y = 3592
x = 3526
y = 3593
x = 3526
y = 3594
x = 3526
y = 3595
x = 3526
y = 3596
x = 3526
y = 3597
x = 3526
y = 3598
x = 3526
y = 3599
x = 3526
y = 3600
x = 3526
y = 3601
x = 3526
y = 3602
x = 3526
y

x = 3526
y = 4212
x = 3526
y = 4213
x = 3526
y = 4214
x = 3526
y = 4215
x = 3526
y = 4216
x = 3526
y = 4217
x = 3526
y = 4218
x = 3526
y = 4219
x = 3526
y = 4220
x = 3526
y = 4221
x = 3526
y = 4222
x = 3526
y = 4223
x = 3526
y = 4224
x = 3526
y = 4225
x = 3526
y = 4226
x = 3526
y = 4227
x = 3526
y = 4228
x = 3526
y = 4229
x = 3526
y = 4230
x = 3526
y = 4231
x = 3526
y = 4232
x = 3526
y = 4233
x = 3526
y = 4234
x = 3526
y = 4235
x = 3526
y = 4236
x = 3526
y = 4237
x = 3526
y = 4238
x = 3526
y = 4239
x = 3526
y = 4240
x = 3526
y = 4241
x = 3526
y = 4242
x = 3526
y = 4243
x = 3526
y = 4244
x = 3526
y = 4245
x = 3526
y = 4246
x = 3526
y = 4247
x = 3526
y = 4248
x = 3526
y = 4249
x = 3526
y = 4250
x = 3526
y = 4251
x = 3526
y = 4252
x = 3526
y = 4253
x = 3526
y = 4254
x = 3526
y = 4255
x = 3526
y = 4256
x = 3526
y = 4257
x = 3526
y = 4258
x = 3526
y = 4259
x = 3526
y = 4260
x = 3526
y = 4261
x = 3526
y = 4262
x = 3526
y = 4263
x = 3526
y = 4264
x = 3526
y = 4265
x = 3526
y = 4266
x = 3526
y

KeyboardInterrupt: 

In [47]:
df_compact = pd.DataFrame(columns=['x','y','area','intensity'])
df_compact

Empty DataFrame
Columns: [x, y, area, intensity]
Index: []